# Your First RAG Application

In this notebook, we'll walk you through each of the components that are involved in a simple RAG application.

We won't be leveraging any fancy tools, just the OpenAI Python SDK, Numpy, and some classic Python.

> NOTE: This was done with Python 3.11.4.

> NOTE: There might be [compatibility issues](https://github.com/wandb/wandb/issues/7683) if you're on NVIDIA driver >552.44 As an interim solution - you can rollback your drivers to the 552.44.

## Table of Contents:

- Task 1: Imports and Utilities
- Task 2: Documents
- Task 3: Embeddings and Vectors
- Task 4: Prompts
- Task 5: Retrieval Augmented Generation
  - 🚧 Activity #1: Augment RAG

Let's look at a rather complicated looking visual representation of a basic RAG application.

<img src="https://i.imgur.com/vD8b016.png" />

## Task 1: Imports and Utility

We're just doing some imports and enabling `async` to work within the Jupyter environment here, nothing too crazy!

In [4]:
from aimakerspace.text_utils import TextFileLoader, CharacterTextSplitter
from aimakerspace.vectordatabase import VectorDatabase
import asyncio

In [5]:
import nest_asyncio
nest_asyncio.apply()

## Task 2: Documents

We'll be concerning ourselves with this part of the flow in the following section:

<img src="https://i.imgur.com/jTm9gjk.png" />

### Loading Source Documents

So, first things first, we need some documents to work with.

While we could work directly with the `.txt` files (or whatever file-types you wanted to extend this to) we can instead do some batch processing of those documents at the beginning in order to store them in a more machine compatible format.

In this case, we're going to parse our text file into a single document in memory.

Let's look at the relevant bits of the `TextFileLoader` class:

```python
def load_file(self):
        with open(self.path, "r", encoding=self.encoding) as f:
            self.documents.append(f.read())
```

We're simply loading the document using the built in `open` method, and storing that output in our `self.documents` list.

> NOTE: We're using blogs from PMarca (Marc Andreessen) as our sample data. This data is largely irrelevant as we want to focus on the mechanisms of RAG, which includes out data's shape and quality - but not specifically what the contents of the data are. 


In [9]:
text_loader = TextFileLoader("data/PMarcaBlogs.txt")
documents = text_loader.load_documents()
len(documents)

1

In [10]:
print(documents[0][:100])


The Pmarca Blog Archives
(select posts from 2007-2009)
Marc Andreessen
copyright: Andreessen Horow


### Splitting Text Into Chunks

As we can see, there is one massive document.

We'll want to chunk the document into smaller parts so it's easier to pass the most relevant snippets to the LLM.

There is no fixed way to split/chunk documents - and you'll need to rely on some intuition as well as knowing your data *very* well in order to build the most robust system.

For this toy example, we'll just split blindly on length.

>There's an opportunity to clear up some terminology here, for this course we will be stick to the following:
>
>- "source documents" : The `.txt`, `.pdf`, `.html`, ..., files that make up the files and information we start with in its raw format
>- "document(s)" : single (or more) text object(s)
>- "corpus" : the combination of all of our documents

As you can imagine (though it's not specifically true in this toy example) the idea of splitting documents is to break them into managable sized chunks that retain the most relevant local context.

In [11]:
text_splitter = CharacterTextSplitter()
split_documents = text_splitter.split_texts(documents)
len(split_documents)

373

Let's take a look at some of the documents we've managed to split.

In [12]:
split_documents[0:1]

['\ufeff\nThe Pmarca Blog Archives\n(select posts from 2007-2009)\nMarc Andreessen\ncopyright: Andreessen Horowitz\ncover design: Jessica Hagy\nproduced using: Pressbooks\nContents\nTHE PMARCA GUIDE TO STARTUPS\nPart 1: Why not to do a startup 2\nPart 2: When the VCs say "no" 10\nPart 3: "But I don\'t know any VCs!" 18\nPart 4: The only thing that matters 25\nPart 5: The Moby Dick theory of big companies 33\nPart 6: How much funding is too little? Too much? 41\nPart 7: Why a startup\'s initial business plan doesn\'t\nmatter that much\n49\nTHE PMARCA GUIDE TO HIRING\nPart 8: Hiring, managing, promoting, and Dring\nexecutives\n54\nPart 9: How to hire a professional CEO 68\nHow to hire the best people you\'ve ever worked\nwith\n69\nTHE PMARCA GUIDE TO BIG COMPANIES\nPart 1: Turnaround! 82\nPart 2: Retaining great people 86\nTHE PMARCA GUIDE TO CAREER, PRODUCTIVITY,\nAND SOME OTHER THINGS\nIntroduction 97\nPart 1: Opportunity 99\nPart 2: Skills and education 107\nPart 3: Where to go and wh

## Task 3: Embeddings and Vectors

Next, we have to convert our corpus into a "machine readable" format as we explored in the Embedding Primer notebook.

Today, we're going to talk about the actual process of creating, and then storing, these embeddings, and how we can leverage that to intelligently add context to our queries.

### OpenAI API Key

In order to access OpenAI's APIs, we'll need to provide our OpenAI API Key!

You can work through the folder "OpenAI API Key Setup" for more information on this process if you don't already have an API Key!

In [3]:
import os
import openai
from getpass import getpass

openai.api_key = getpass("OpenAI API Key: ")
os.environ["OPENAI_API_KEY"] = openai.api_key

### Vector Database

Let's set up our vector database to hold all our documents and their embeddings!

While this is all baked into 1 call - we can look at some of the code that powers this process to get a better understanding:

Let's look at our `VectorDatabase().__init__()`:

```python
def __init__(self, embedding_model: EmbeddingModel = None):
        self.vectors = defaultdict(np.array)
        self.embedding_model = embedding_model or EmbeddingModel()
```

As you can see - our vectors are merely stored as a dictionary of `np.array` objects.

Secondly, our `VectorDatabase()` has a default `EmbeddingModel()` which is a wrapper for OpenAI's `text-embedding-3-small` model.

> **Quick Info About `text-embedding-3-small`**:
> - It has a context window of **8191** tokens
> - It returns vectors with dimension **1536**

#### ❓Question #1:

The default embedding dimension of `text-embedding-3-small` is 1536, as noted above. 

1. Is there any way to modify this dimension?
2. What technique does OpenAI use to achieve this?

> NOTE: Check out this [API documentation](https://platform.openai.com/docs/api-reference/embeddings/create) for the answer to question #1, and [this documentation](https://platform.openai.com/docs/guides/embeddings/use-cases) for an answer to question #2!

### ✅ ANSWER
**1. Is there any way to modify this dimension?**

> Yes, it is possible to modify the dimension of the output embedding. However, when doing so you lose meaning behind the characters and words in the text that you are embedding so be cautious. Below is an example of how to modify the dimension in code.

In [5]:
from openai import OpenAI

client = OpenAI()
response = client.embeddings.create(
    model="text-embedding-3-small", input="Testing 123", encoding_format="float", dimensions=10
)
print(len(response.data[0].embedding))
print(response.data[0].embedding)

10
[-0.4249391, -0.20683408, 0.6815333, -0.46402773, -0.015962195, 0.09742185, 0.2392081, 0.09442425, 0.14448409, -0.008902858]


### ✅ ANSWER
**2. What technique does OpenAI use to achieve this?**

Open AI uses **matryoshka representation learning** to change the dimensions of embeddings generated by it's model. The embeddings are structured in a way that the most essential semantics are stored at the beggining of the vector.

If you need a smaller embedding vector due to size constraints just cut off the later elements of the vector. Or to optimize for performance try using the the shorter, earlier parts of the embedding for an initial fast search, and then use the entire vector for more granual search.

We can call the `async_get_embeddings` method of our `EmbeddingModel()` on a list of `str` and receive a list of `float` back!

```python
async def async_get_embeddings(self, list_of_text: List[str]) -> List[List[float]]:
        return await aget_embeddings(
            list_of_text=list_of_text, engine=self.embeddings_model_name
        )
```

We cast those to `np.array` when we build our `VectorDatabase()`:

```python
async def abuild_from_list(self, list_of_text: List[str]) -> "VectorDatabase":
        embeddings = await self.embedding_model.async_get_embeddings(list_of_text)
        for text, embedding in zip(list_of_text, embeddings):
            self.insert(text, np.array(embedding))
        return self
```

And that's all we need to do!

In [15]:
vector_db = VectorDatabase()
vector_db = asyncio.run(vector_db.abuild_from_list(split_documents))

#### ❓Question #2:

What are the benefits of using an `async` approach to collecting our embeddings?

> NOTE: Determining the core difference between `async` and `sync` will be useful! If you get stuck - ask ChatGPT!

### ✅ ANSWER

`sync` and `async` refer to different approaches to completing a collection of tasks. For `sync` or `syncronous` when one task is started, the system must wait for its completion before starting the next task. For `async` or `asynchronous` it is possible to complete multiple tasks concurrently. Processing multiple tasks at a time rather than one at a time.

Using an async approach allows us to collect embeddings concurrently, which is especially beneficial when embedding many documents using an API call.

Instead of waiting for each request to finish one after the other, async enables the program to start multiple requests at once, then wait for all of them to complete. This dramatically reduces total runtime.

Benefits:
	•	Faster execution when embedding large batches of text
	•	Better resource usage: CPU/GPU isn’t idle while waiting on network responses
	•	Scales well with large numbers of documents or API calls


So, to review what we've done so far in natural language:

1. We load source documents
2. We split those source documents into smaller chunks (documents)
3. We send each of those documents to the `text-embedding-3-small` OpenAI API endpoint
4. We store each of the text representations with the vector representations as keys/values in a dictionary

### Semantic Similarity

The next step is to be able to query our `VectorDatabase()` with a `str` and have it return to us vectors and text that is most relevant from our corpus.

We're going to use the following process to achieve this in our toy example:

1. We need to embed our query with the same `EmbeddingModel()` as we used to construct our `VectorDatabase()`
2. We loop through every vector in our `VectorDatabase()` and use a distance measure to compare how related they are
3. We return a list of the top `k` closest vectors, with their text representations

There's some very heavy optimization that can be done at each of these steps - but let's just focus on the basic pattern in this notebook.

> We are using [cosine similarity](https://www.engati.com/glossary/cosine-similarity) as a distance metric in this example - but there are many many distance metrics you could use - like [these](https://flavien-vidal.medium.com/similarity-distances-for-natural-language-processing-16f63cd5ba55)

> We are using a rather inefficient way of calculating relative distance between the query vector and all other vectors - there are more advanced approaches that are much more efficient, like [ANN](https://towardsdatascience.com/comprehensive-guide-to-approximate-nearest-neighbors-algorithms-8b94f057d6b6)

In [16]:
vector_db.search_by_text("What is the Michael Eisner Memorial Weak Executive Problem?", k=3)

[('ordingly.\nSeventh, when hiring the executive to run your former specialty, be\ncareful you don’t hire someone weak on purpose.\nThis sounds silly, but you wouldn’t believe how oaen it happens.\nThe CEO who used to be a product manager who has a weak\nproduct management executive. The CEO who used to be in\nsales who has a weak sales executive. The CEO who used to be\nin marketing who has a weak marketing executive.\nI call this the “Michael Eisner Memorial Weak Executive Problem” — aaer the CEO of Disney who had previously been a brilliant TV network executive. When he bought ABC at Disney, it\npromptly fell to fourth place. His response? “If I had an extra\ntwo days a week, I could turn around ABC myself.” Well, guess\nwhat, he didn’t have an extra two days a week.\nA CEO — or a startup founder — oaen has a hard time letting\ngo of the function that brought him to the party. The result: you\nhire someone weak into the executive role for that function so\nthat you can continue to b

## Task 4: Prompts

In the following section, we'll be looking at the role of prompts - and how they help us to guide our application in the right direction.

In this notebook, we're going to rely on the idea of "zero-shot in-context learning".

This is a lot of words to say: "We will ask it to perform our desired task in the prompt, and provide no examples."

### XYZRolePrompt

Before we do that, let's stop and think a bit about how OpenAI's chat models work.

We know they have roles - as is indicated in the following API [documentation](https://platform.openai.com/docs/api-reference/chat/create#chat/create-messages)

There are three roles, and they function as follows (taken directly from [OpenAI](https://platform.openai.com/docs/guides/gpt/chat-completions-api)):

- `{"role" : "developer"}` : The system message helps set the behavior of the assistant. For example, you can modify the personality of the assistant or provide specific instructions about how it should behave throughout the conversation. However note that the system message is optional and the model’s behavior without a system message is likely to be similar to using a generic message such as "You are a helpful assistant."
- `{"role" : "user"}` : The user messages provide requests or comments for the assistant to respond to.
- `{"role" : "assistant"}` : Assistant messages store previous assistant responses, but can also be written by you to give examples of desired behavior.

The main idea is this:

1. You start with a developer message that outlines how the LLM should respond, what kind of behaviours you can expect from it, and more
2. Then, you can provide a few examples in the form of "assistant"/"user" pairs
3. Then, you prompt the model with the true "user" message.

In this example, we'll be forgoing the 2nd step for simplicities sake.

#### Utility Functions

You'll notice that we're using some utility functions from the `aimakerspace` module - let's take a peek at these and see what they're doing!

##### XYZRolePrompt

Here we have our `system`, `user`, and `assistant` role prompts.

Let's take a peek at what they look like:

```python
class BasePrompt:
    def __init__(self, prompt):
        """
        Initializes the BasePrompt object with a prompt template.

        :param prompt: A string that can contain placeholders within curly braces
        """
        self.prompt = prompt
        self._pattern = re.compile(r"\{([^}]+)\}")

    def format_prompt(self, **kwargs):
        """
        Formats the prompt string using the keyword arguments provided.

        :param kwargs: The values to substitute into the prompt string
        :return: The formatted prompt string
        """
        matches = self._pattern.findall(self.prompt)
        return self.prompt.format(**{match: kwargs.get(match, "") for match in matches})

    def get_input_variables(self):
        """
        Gets the list of input variable names from the prompt string.

        :return: List of input variable names
        """
        return self._pattern.findall(self.prompt)
```

Then we have our `RolePrompt` which laser focuses us on the role pattern found in most API endpoints for LLMs.

```python
class RolePrompt(BasePrompt):
    def __init__(self, prompt, role: str):
        """
        Initializes the RolePrompt object with a prompt template and a role.

        :param prompt: A string that can contain placeholders within curly braces
        :param role: The role for the message ('system', 'user', or 'assistant')
        """
        super().__init__(prompt)
        self.role = role

    def create_message(self, **kwargs):
        """
        Creates a message dictionary with a role and a formatted message.

        :param kwargs: The values to substitute into the prompt string
        :return: Dictionary containing the role and the formatted message
        """
        return {"role": self.role, "content": self.format_prompt(**kwargs)}
```

We'll look at how the `SystemRolePrompt` is constructed to get a better idea of how that extension works:

```python
class SystemRolePrompt(RolePrompt):
    def __init__(self, prompt: str):
        super().__init__(prompt, "system")
```

That pattern is repeated for our `UserRolePrompt` and our `AssistantRolePrompt` as well.

##### ChatOpenAI

Next we have our model, which is converted to a format analagous to libraries like LangChain and LlamaIndex.

Let's take a peek at how that is constructed:

```python
class ChatOpenAI:
    def __init__(self, model_name: str = "gpt-4o-mini"):
        self.model_name = model_name
        self.openai_api_key = os.getenv("OPENAI_API_KEY")
        if self.openai_api_key is None:
            raise ValueError("OPENAI_API_KEY is not set")

    def run(self, messages, text_only: bool = True):
        if not isinstance(messages, list):
            raise ValueError("messages must be a list")

        openai.api_key = self.openai_api_key
        response = openai.ChatCompletion.create(
            model=self.model_name, messages=messages
        )

        if text_only:
            return response.choices[0].message.content

        return response
```

#### ❓ Question #3:

When calling the OpenAI API - are there any ways we can achieve more reproducible outputs?

> NOTE: Check out [this section](https://platform.openai.com/docs/guides/text-generation/) of the OpenAI documentation for the answer!

### ✅ ANSWER
- Using the instructions field, instruct the LLM to provide it's output in a given format such as JSON. Provide an example of kind of value you expect for each field. You can also specify goals and the expected tone.
- Pin your production application to a specific model snapshot to avoid various due to model updates

### Creating and Prompting OpenAI's `gpt-4o-mini`!

Let's tie all these together and use it to prompt `gpt-4o-mini`!

In [8]:
from aimakerspace.openai_utils.prompts import (
    UserRolePrompt,
    SystemRolePrompt,
    AssistantRolePrompt,
)

from aimakerspace.openai_utils.chatmodel import ChatOpenAI

chat_openai = ChatOpenAI()
user_prompt_template = "{content}"
user_role_prompt = UserRolePrompt(user_prompt_template)
system_prompt_template = (
    "You are an expert in {expertise}, you always answer in a kind way."
)
system_role_prompt = SystemRolePrompt(system_prompt_template)

messages = [
    system_role_prompt.create_message(expertise="Python"),
    user_role_prompt.create_message(
        content="What is the best way to write a loop?"
    ),
]

response = chat_openai.run(messages)

In [18]:
print(response)

The best way to write a loop in Python depends on what you are trying to achieve. However, there are some general best practices that can help you write clear and efficient loops. Here are a few options along with examples to illustrate:

### 1. Using `for` loops

`for` loops are often considered the most Pythonic way to iterate over items in a sequence (like lists, tuples, or strings):

```python
# Example: iterate through a list
fruits = ['apple', 'banana', 'cherry']
for fruit in fruits:
    print(fruit)
```

### 2. Using `while` loops

`while` loops are useful when the number of iterations is not known in advance and you want to continue looping until a certain condition is met:

```python
# Example: using a while loop
count = 0
while count < 5:
    print(count)
    count += 1
```

### 3. Using `enumerate`

When you need both the index and the value while iterating, you can use `enumerate()`:

```python
# Example: using enumerate to get index and value
for index, fruit in enumerate(

## Task 5: Retrieval Augmented Generation

Now we can create a RAG prompt - which will help our system behave in a way that makes sense!

There is much you could do here, many tweaks and improvements to be made!

In [12]:
RAG_SYSTEM_TEMPLATE = """You are a knowledgeable assistant that answers questions based strictly on provided context.

Instructions:
- Only answer questions using information from the provided context
- If the context doesn't "I don't know"
- Be accurate and cite specific parts of the context when possible
- Keep responses {response_style} and {response_length}
- Only use the provided context. Do not use external knowledge.
- Only provide answers when you are confident the context supports your response."""

RAG_USER_TEMPLATE = """Context Information:
{context}

Number of relevant sources found: {context_count}
{similarity_scores}

Question: {user_query}

Please provide your answer based solely on the context above."""

rag_system_prompt = SystemRolePrompt(
    RAG_SYSTEM_TEMPLATE,
    strict=True,
    defaults={
        "response_style": "concise",
        "response_length": "brief"
    }
)

rag_user_prompt = UserRolePrompt(
    RAG_USER_TEMPLATE,
    strict=True,
    defaults={
        "context_count": "",
        "similarity_scores": ""
    }
)

Now we can create our pipeline!

In [10]:
class RetrievalAugmentedQAPipeline:
    def __init__(self, llm: ChatOpenAI(), vector_db_retriever: VectorDatabase, 
                 response_style: str = "detailed", include_scores: bool = False) -> None:
        self.llm = llm
        self.vector_db_retriever = vector_db_retriever
        self.response_style = response_style
        self.include_scores = include_scores

    def run_pipeline(self, user_query: str, k: int = 4, **system_kwargs) -> dict:
        # Retrieve relevant contexts
        context_list = self.vector_db_retriever.search_by_text(user_query, k=k)
        
        context_prompt = ""
        similarity_scores = []
        
        for i, (context, score) in enumerate(context_list, 1):
            context_prompt += f"[Source {i}]: {context}\n\n"
            similarity_scores.append(f"Source {i}: {score:.3f}")
        
        # Create system message with parameters
        system_params = {
            "response_style": self.response_style,
            "response_length": system_kwargs.get("response_length", "detailed")
        }
        
        formatted_system_prompt = rag_system_prompt.create_message(**system_params)
        
        user_params = {
            "user_query": user_query,
            "context": context_prompt.strip(),
            "context_count": len(context_list),
            "similarity_scores": f"Relevance scores: {', '.join(similarity_scores)}" if self.include_scores else ""
        }
        
        formatted_user_prompt = rag_user_prompt.create_message(**user_params)

        return {
            "response": self.llm.run([formatted_system_prompt, formatted_user_prompt]), 
            "context": context_list,
            "context_count": len(context_list),
            "similarity_scores": similarity_scores if self.include_scores else None,
            "prompts_used": {
                "system": formatted_system_prompt,
                "user": formatted_user_prompt
            }
        }

In [21]:
rag_pipeline = RetrievalAugmentedQAPipeline(
    vector_db_retriever=vector_db,
    llm=chat_openai,
    response_style="detailed",
    include_scores=True
)

result = rag_pipeline.run_pipeline(
    "What is the 'Michael Eisner Memorial Weak Executive Problem'?",
    k=3,
    response_length="comprehensive", 
    include_warnings=True,
    confidence_required=True
)

print(f"Response: {result['response']}")
print(f"\nContext Count: {result['context_count']}")
print(f"Similarity Scores: {result['similarity_scores']}")


Response: The 'Michael Eisner Memorial Weak Executive Problem' refers to the tendency of CEOs or startup founders to hire executives who are weak in the functions that they themselves excelled at, in order to maintain control and continue being the dominant force in that area. This phenomenon is highlighted through the example of Michael Eisner, the former CEO of Disney, who, despite being a brilliant TV network executive, had a weak executive managing ABC after its acquisition, which ultimately fell to fourth place. His inability to delegate effectively led him to believe that he could turn ABC around himself if he simply had more time, which he did not have. The context suggests that this issue arises because the individuals in such positions often struggle to let go of the functions that were pivotal to their rise, resulting in hiring choices that undermine their business.

Context Count: 3
Similarity Scores: ['Source 1: 0.658', 'Source 2: 0.509', 'Source 3: 0.479']


#### ❓ Question #4:

What prompting strategies could you use to make the LLM have a more thoughtful, detailed response?

What is that strategy called?

> NOTE: You can look through ["Accessing GPT-3.5-turbo Like a Developer"](https://colab.research.google.com/drive/1mOzbgf4a2SP5qQj33ZxTz2a01-5eXqk2?usp=sharing) for an answer to this question if you get stuck!

### ✅ ANSWER
The strategy is called chain-of-thought prompting. It a technique that involves either telling the LLM to think step by step when generating the response. The LLM will then take additional time / tokens to first create a plan, and then use the plan to solve the problem. By doing this it is able to solve more complex problems and generate a response that guides the user through how it was accomplished resulting in a more detailed response.

You can also give the LLM a plan to follow and it will do so step by step.

Some other helpful approaches:
- Ask the LLM to "Explain your answer in detail" or "List all the steps you would take"
- Ask the model to generate follow-up questions and answer them

### 🏗️ Activity #1:

Enhance your RAG application in some way! 

Suggestions are: 

- Allow it to work with PDF files
- Implement a new distance metric
- Add metadata support to the vector database

While these are suggestions, you should feel free to make whatever augmentations you desire! 

> NOTE: These additions might require you to work within the `aimakerspace` library - that's expected!

> NOTE: If you're not sure where to start - ask Cursor (CMD/CTRL+L) to guide you through the changes!

# RAG ENHANCEMENTS: ANSWER IN THE CELLS THAT FOLLOW

### The Enhancement include:
1. Allowing RAG on PDF Files
2. Chunking content based on location of paragraphs, punctuation, etc by using the Recursive Character Text Splitter. Preserves logical units of text and avoids chopping sentences and ideas awkardly.
3. Re Ranking Approach to Chunk Retrieval
4. [Attempted but not completed] Metadata Filtering on Chunks

## Helper Functions for Displaying Chunks

In [62]:
from IPython.display import Markdown, display

def print_context_list_as_markdown(context_list):
    print(f"Context List: {context_list}")
    for context in context_list:
        print(f"score: {context[1]}")
        display(Markdown(context[0]))


def print_pipeline_results(results, only_response=False):
    print(f"Response:")
    display(Markdown(results['response']))
    if only_response:
        return
    print(f"\nContext Count: {result['context_count']}")
    print(f"Similarity Scores: {result['similarity_scores']}")

    for index, context in enumerate(results['context']):
        print(f"context {index+1}:")
        display(Markdown(context[0]))
        print(f"score: {context[1]}")


In [35]:
import os
import openai
from getpass import getpass

openai.api_key = getpass("OpenAI API Key: ")
os.environ["OPENAI_API_KEY"] = openai.api_key

## Loading PDF Contents

In [36]:
# Loading the Contents of the PDF
import pdfplumber
class PDFFileLoader:
    def __init__(self, path):
        self.path = path
        self.documents = []

    def load_file(self):
        with pdfplumber.open(self.path) as pdf:
            text = "\n".join(page.extract_text() for page in pdf.pages if page.extract_text())
            self.documents.append(text)
        return self.documents
    
file_loader = PDFFileLoader("data/Fundementals of Python_ DSA [2nd Edition].pdf")
documents_from_pdf = file_loader.load_file()

Cannot set gray non-stroke color because /'P0' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P2' is an invalid float value
Cannot set gray non-stroke color because /'P0' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P2' is an invalid float value
Cannot set gray non-stroke color because /'P3' is an invalid float value
Cannot set gray non-stroke color because /'P4' is an invalid float value
Cannot set gray non-stroke color because /'P0' is an invalid float value


1891

### Chunking using RecursiveCharacterText Splitter

In [37]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
split_pdf_documents = text_splitter.split_text(documents_from_pdf[0])
len(split_pdf_documents)

1891

### Loading Chunks into Vector Store

In [38]:
vector_db_from_pdf = VectorDatabase()
vector_db_from_pdf = asyncio.run(vector_db_from_pdf.abuild_from_list(split_pdf_documents))

### Retrieval Re-ranking
NOTE: I also experimented with using different similarity formula's such as Manhattan and Euclidean Distance

In [60]:
from aimakerspace.vectordatabase import VectorDatabase
from aimakerspace.openai_utils.chatmodel import ChatOpenAI

class ReRankingRetrievalAugmentedQAPipeline:
    def __init__(
        self,
        llm: ChatOpenAI,
        vector_db_retriever: VectorDatabase,
        response_style: str = "detailed",
        include_scores: bool = False,
        cross_encoder=None,  # <-- NEW: Cross-encoder for re-ranking
        embedding_model=None # <-- NEW: Bi-encoder for embedding queries
    ) -> None:
        self.llm = llm
        self.vector_db_retriever = vector_db_retriever
        self.response_style = response_style
        self.include_scores = include_scores
        self.cross_encoder = cross_encoder

    def run_pipeline(self, user_query: str, k: int = 4, **system_kwargs) -> dict:
        # ----- Stage 1: Retrieve Top-K with Bi-Encoder -----
        # Get top-k docs (text, score) using vector search
        context_list = self.vector_db_retriever.search_by_text(user_query, k=k)
        top_k_docs = [context for context, _ in context_list]

        # ----- Stage 2: Cross-Encoder Re-Ranking -----
        if self.cross_encoder is not None:
            cross_input = [(user_query, doc) for doc in top_k_docs]
            cross_scores = self.cross_encoder.predict(cross_input)
            reranked = sorted(zip(top_k_docs, cross_scores), key=lambda x: x[1], reverse=True)
            # Optionally, update context_list with reranked order and scores
            context_list = [(doc, float(score)) for doc, score in reranked]

        # ----- Prompt Construction (as before) -----
        context_prompt = ""
        similarity_scores = []
        for i, (context, score) in enumerate(context_list, 1):
            context_prompt += f"[Source {i}]: {context}\n\n"
            similarity_scores.append(f"Source {i}: {score:.3f}")

        system_params = {
            "response_style": self.response_style,
            "response_length": system_kwargs.get("response_length", "detailed")
        }
        formatted_system_prompt = rag_system_prompt.create_message(**system_params)

        user_params = {
            "user_query": user_query,
            "context": context_prompt.strip(),
            "context_count": len(context_list),
            "similarity_scores": f"Relevance scores: {', '.join(similarity_scores)}" if self.include_scores else ""
        }
        formatted_user_prompt = rag_user_prompt.create_message(**user_params)

        return {
            "response": self.llm.run([formatted_system_prompt, formatted_user_prompt]), 
            "context": context_list,
            "context_count": len(context_list),
            "similarity_scores": similarity_scores if self.include_scores else None,
            "prompts_used": {
                "system": formatted_system_prompt,
                "user": formatted_user_prompt
            }
        }

### Let's try it out!

In [63]:

pdf_rag_pipeline = ReRankingRetrievalAugmentedQAPipeline(
    vector_db_retriever=vector_db_from_pdf,
    llm=chat_openai,
    response_style="detailed",
    include_scores=True
)

result = pdf_rag_pipeline.run_pipeline(
    "Help me understand the time and space complexity of a binary search tree",
    k=3,
    response_length="comprehensive", 
    include_warnings=True,
    confidence_required=True
)

print_pipeline_results(result, only_response=True)

Response:


The time complexity of searching in a binary search tree (BST) is primarily influenced by the height of the tree (denoted as h). According to the context, the worst-case running time of searching within a binary search tree using the recursive algorithm TreeSearch is O(h). This is because TreeSearch executes a constant number of primitive operations (O(1)) for each recursive call made on a child of the previous position along a path from the root down to a leaf, resulting in a total time complexity of O(h) for the search operation.

Additionally, various operations associated with the sorted map Abstract Data Type (ADT), such as getitem, setitem, and delitem, also begin with a search for an existing item based on a given key, thus running in worst-case O(h) time as well. The implementation of methods like find lt and find gt incorporates this search along with traversal methods and maintains an O(h) time complexity (see the second source).

While the height h of the tree could potentially reach the number of entries n, it is generally expected to be much smaller, especially in a balanced tree scenario. It is stated that the maximum path length within the tree is proportional to its height, confirming the dependency of most operations on h (Source 3).

Regarding space complexity, the context does not provide specific information about space complexity in terms of memory usage or additional data structures utilized during the search or other operations in the binary search tree. Therefore, I cannot determine the space complexity based solely on the provided context. 

In summary, the time complexity for search-related operations in a binary search tree is O(h), where h is the height of the tree, while information on space complexity is not available in the context provided.

In [59]:
result = pdf_rag_pipeline.run_pipeline(
    "What's the code for implementing a Sorted Priority Queue?",
    k=5,
    response_length="comprehensive", 
    include_warnings=True,
    confidence_required=True
)

print_pipeline_results(result)

Response:


The implementation of a Sorted Priority Queue is provided in Source 1. Here is the code:

```python
class SortedPriorityQueue(PriorityQueueBase):  # base class defines Item
    """A min-oriented priority queue implemented with a sorted list."""

    def __init__(self):
        """Create a new empty Priority Queue."""
        self.data = PositionalList()

    def len(self):
        """Return the number of items in the priority queue."""
        return len(self.data)

    def add(self, key, value):
        """Add a key-value pair."""
        newest = self.Item(key, value)  # make new item instance
        walk = self.data.last()  # walk backward looking for smaller key
        while walk is not None and newest < walk.element():
            walk = self.data.before(walk)
        if walk is None:
            self.data.add_first(newest)  # new key is smallest
        else:
            self.data.add_after(walk, newest)  # newest goes after walk

    def min(self):
        """Return but do not remove (k,v) tuple with minimum key."""
        if self.is_empty():
            raise Empty("Priority queue is empty.")
        # Implementation to retrieve the minimum would follow
```

This implementation uses a `PositionalList` to store the key-value pairs and maintains the items in a sorted manner. The `add()` method ensures that new items are inserted in the correct position based on their keys.


Context Count: 5
Similarity Scores: ['Source 1: 0.638', 'Source 2: 0.613', 'Source 3: 0.604', 'Source 4: 0.582', 'Source 5: 0.581']
context 1:


listisimplemented byadoubly linkedlist. Thespacerequirement isO(n).
9.2. ImplementingaPriorityQueue 369
1 class SortedPriorityQueue(PriorityQueueBase): # base class defines Item
2 ”””A min-oriented priority queue implemented with a sorted list.”””
3
4 def init (self):
5 ”””Create a new empty Priority Queue.”””
6 self. data = PositionalList()
7
8 def len (self):
9 ”””Return the number of items in the priority queue.”””
10 return len(self. data)
11
12 def add(self, key, value):
13 ”””Add a key-value pair.”””
14 newest = self. Item(key, value) # make new item instance
15 walk = self. data.last( ) # walk backward looking for smaller key
16 while walk is not None and newest < walk.element():
17 walk = self. data.before(walk)
18 if walk is None:
19 self. data.add first(newest) # new key is smallest
20 else:
21 self. data.add after(walk, newest) # newest goes after walk
22
23 def min(self):
24 ”””Return but do not remove (k,v) tuple with minimum key.”””
25 if self.is empty():

score: 0.6381843372742128
context 2:


...

score: 0.6037561387531428
context 4:


9.5.1 Locators . . . . . . . . . . . . . . . . . . . . . . . . . . . 390
9.5.2 Implementing an Adaptable Priority Queue . . . . . . . . 391
9.6 Exercises . . . . . . . . . . . . . . . . . . . . . . . . . . . . 395
9.1. ThePriorityQueueAbstractDataType 363
9.1 The Priority Queue Abstract Data Type
9.1.1 Priorities
In Chapter 6, we introduced the queue ADT as a collection of objects that are
added and removed according to the first-in, first-out (FIFO) principle. A com-
pany’scustomercallcenterembodiessuchamodelinwhichwaitingcustomersare
told“calls willbeanswered intheorderthattheywerereceived.” Inthatsetting, a
new call is added to the back of the queue, and each time a customer service rep-
resentative becomes available, he orsheisconnected withthecall that isremoved
fromthefrontofthecallqueue.
Inpractice, therearemanyapplications inwhichaqueue-like structure isused
to manage objects that must be processed in some way, but for which the first-in,

score: 0.5820838164637382
context 5:


Code Fragment 9.4: An implementation of a priority queue using an array-based
heap (continued inCode Fragment 9.5). Theextends thePriorityQueueBaseclass
fromCodeFragment9.1.
378 Chapter9. PriorityQueues
40 #------------------------------ public behaviors ------------------------------
41 def init (self):
42 ”””Create a new empty Priority Queue.”””
43 self. data = [ ]
44
45 def len (self):
46 ”””Return the number of items in the priority queue.”””
47 return len(self. data)
48
49 def add(self, key, value):
50 ”””Add a key-value pair to the priority queue.”””
51 self. data.append(self. Item(key, value))
52 self. upheap(len(self. data) − 1) # upheap newly added position
53
54 def min(self):
55 ”””Return but do not remove (k,v) tuple with minimum key.
56
57 Raise Empty exception if empty.
58 ”””
59 if self.is empty():
60 raise Empty( Priority queue is empty. )
61 item = self. data[0]
62 return (item. key, item. value)
63
64 def remove min(self):

score: 0.5812398495845585


## YOU NEED NOT RUN WHAT IS BELOW. EXPERIMENTATION PROCESS ONLY

In [64]:
from pdfminer.high_level import extract_text

def load_pdf_with_pdfminer(path):
    text = extract_text(path)
    return text

pdf_path = "data/Fundementals of Python_ DSA [2nd Edition].pdf"
pdf_text = load_pdf_with_pdfminer(pdf_path)
print(pdf_text[20000:21000])  # Print the first 1000 characters to check extraction

Cannot set gray non-stroke color because /'P0' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P2' is an invalid float value
Cannot set gray non-stroke color because /'P0' is an invalid float value
Cannot set gray non-stroke color because /'P1' is an invalid float value
Cannot set gray non-stroke color because /'P2' is an invalid float value
Cannot set gray non-stroke color because /'P3' is an invalid float value
Cannot set gray non-stroke color because /'P4' is an invalid float value
Cannot set gray non-stroke color because /'P0' is an invalid float value


opment

2.1 Goals, Principles, and Patterns

. . . . . . . . . . . . . . . .
. . . . . . . . . . . . . .
2.1.1 Object-Oriented Design Goals
. . . . . . . . . . . .
2.1.2 Object-Oriented Design Principles
2.1.3 Design Patterns . . . . . . . . . . . . . . . . . . . . . .
. . . . . . . . . . . . . . . . . . . . .
2.2.1 Design . . . . . . . . . . . . . . . . . . . . . . . . . . .
. . . . . . . . . . . . . . . . . . . . . . .
2.2.2 Pseudo-Code
2.2.3 Coding Style and Documentation . . . . . . . . . . . . .
2.2.4 Testing and Debugging . . . . . . . . . . . . . . . . . .
2.3 Class Deﬁnitions . . . . . . . . . . . . . . . . . . . . . . . . .
2.3.1 Example: CreditCard Class . . . . . . . . . . . . . . . .
2.3.2 Operator Overloading and Python’s Special Methods . .
2.3.3 Example: Multidimensional Vector Class . . . . . . . . .
Iterators . . . . . . . . . . . . . . . . . . . . . . . . . .
2.3.4
2.3.5 Example: Range Class . . . . . . . . . . . . . . . . . . .
2.4 Inheritance . . . . . . . . . . . .

In [65]:
print(pdf_text[110000:150000])

ation on the same line, it is
common to call the split method on the result, as in

reply = input( Enter x and y, separated by spaces: )
pieces = reply.split( ) # returns a list of strings, as separated by spaces
x = ﬂoat(pieces[0])
y = ﬂoat(pieces[1])

A Sample Program

Here is a simple, but complete, program that demonstrates the use of the input
and print functions. The tools for formatting the ﬁnal output is discussed in Ap-
pendix A.

age = int(input( Enter your age in years: ))
max heart rate = 206.9 − (0.67
target = 0.65 max heart rate
print( Your target fat-burning heart rate is , target)

age) # as per Med Sci Sports Exerc.

1.6.2 Files

Files are typically accessed in Python beginning with a call to a built-in function,
named open, that returns a proxy for interactions with the underlying ﬁle. For
example, the command, fp = open( sample.txt ), attempts to open a ﬁle named
sample.txt, returning a proxy that allows read-only access to the text ﬁle.

The open function accepts an

# Experimenting with RecursiveCharacterTextSplitter

In [143]:
# text_splitter = CharacterTextSplitter()
# split_pdf_documents_miner = text_splitter.split_texts(pdf_text)
# len(split_pdf_documents_miner)

from langchain.text_splitter import RecursiveCharacterTextSplitter

splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
chunks = splitter.split_text(pdf_text)
len(chunks)




2230

In [145]:
print(chunks[1000])

else:

parent. right = child

self. size −= 1
node. parent = node
return node. element

def attach(self, p, t1, t2):

# child becomes root

# convention for deprecated node

”””Attach trees t1 and t2 as left and right subtrees of external p.”””
node = self. validate(p)
if not self.is leaf(p): raise ValueError( position must be leaf )
if not type(self) is type(t1) is type(t2): # all 3 trees must be same type

raise TypeError( Tree types must match )

self. size += len(t1) + len(t2)
if not t1.is empty( ):

t1. root. parent = node
node. left = t1. root
t1. root = None
t1. size = 0

# attached t1 as left subtree of node

# set t1 instance to empty

if not t2.is empty( ):

# attached t2 as right subtree of node

t2. root. parent = node
node. right = t2. root
t2. root = None
t2. size = 0

# set t2 instance to empty

Code Fragment 8.11: Nonpublic update methods for the LinkedBinaryTree class
(continued from Code Fragment 8.10).


324

Chapter8. Trees


In [152]:
vector_db_from_pdf_miner = VectorDatabase()
vector_db_from_pdf_miner = asyncio.run(vector_db_from_pdf_miner.abuild_from_list(chunks))
                                       
pdf_rag_pipeline = RetrievalAugmentedQAPipeline(
    vector_db_retriever=vector_db_from_pdf_miner,
    llm=chat_openai,
    response_style="detailed",
    include_scores=True
)

In [169]:
result = pdf_rag_pipeline.run_pipeline(
    "What ADT can be used to represent a network",
    k=3,
    response_length="comprehensive", 
    include_warnings=True,
    confidence_required=True
)

print_pipeline_results(result)

Response:


The context suggests that a graph can be used to represent a network. Specifically, it mentions "Physical examples of graphs are present in the electrical wiring and plumbing networks of a building" (Source 2), indicating that such networks can be modeled as graphs with vertices representing connectors, fixtures, or outlets, and edges representing uninterrupted stretches of wire or pipe.


Context Count: 3
Similarity Scores: ['Source 1: 0.411', 'Source 2: 0.382', 'Source 3: 0.381']
context 1:


• If G isconnected, then m ≥ n − 1.
• If G isatree, then m = n − 1.
• If G isaforest, then m ≤ n − 1.


626

Chapter14. GraphAlgorithms

14.1.1 The Graph ADT

A graph is a collection of vertices and edges. We model the abstraction as a com-
bination of three data types: Vertex, Edge, and Graph. A Vertex is a lightweight
object that stores an arbitrary element provided by the user (e.g., an airport code);
we assume it supports a method, element( ), to retrieve the stored element. An
Edge also stores an associated object (e.g., a ﬂight number, travel distance, cost),
retrieved with the element( ) method. In addition, we assume that an Edge supports
the following methods:

endpoints( ): Return a tuple (u, v) such that vertex u is the origin of
the edge and vertex v is the destination; for an undirected
graph, the orientation is arbitrary.

opposite(v): Assuming vertex v is one endpoint of the edge (either

origin or destination), return the other endpoint.

score: 0.4109524814642883
context 2:


Example 14.4: Physical examples of graphs are present in the electrical wiring
and plumbing networks of a building. Such networks can be modeled as graphs,
where each connector, ﬁxture, or outlet is viewed as a vertex, and each uninter-
rupted stretch of wireor pipe isviewed asan edge. Such graphs are actually com-
ponents of much larger graphs, namely the local power and water distribution net-
works. Depending onthe speciﬁc aspects ofthese graphs thatweare interested in,
we may consider their edges as undirected or directed, for, in principle, water can
ﬂowinapipeandcurrent canﬂowinawireineither direction.

score: 0.38179123340551874
context 3:


7.4. ThePositionalListADT

277

7.4 The Positional List ADT

The abstract data types that we have considered thus far, namely stacks, queues,
and double-ended queues, only allow update operations that occur at one end of a
sequence or the other. We wish to have a more general abstraction. For example,
although we motivated the FIFO semantics of a queue as a model for customers
who are waiting to speak with a customer service representative, or fans who are
waiting in line to buy tickets to a show, the queue ADT is too limiting. What if
a waiting customer decides to hang up before reaching the front of the customer
service queue? Or what if someone who is waiting in line to buy tickets allows a
friend to “cut” into line at that position? We would like to design an abstract data
type that provides a user a way to refer to elements anywhere in a sequence, and to
perform arbitrary insertions and deletions.

score: 0.3809485664030642


# Experimenting with Different Similarity Measures

In [183]:
import numpy as np

def euclidean_similarity(vector_a: np.array, vector_b: np.array) -> float:
    """Computes the inverse of Euclidean distance as a similarity measure."""
    distance = np.linalg.norm(vector_a - vector_b)
    return 1 / (1 + distance)  # to keep it bounded and non-infinite

def manhattan_similarity(vector_a: np.array, vector_b: np.array) -> float:
    """Computes the inverse of Manhattan distance as a similarity measure."""
    distance = np.sum(np.abs(vector_a - vector_b))
    return 1 / (1 + distance)  # same idea: convert distance to similarity

In [184]:
from aimakerspace.vectordatabase import cosine_similarity
cosine_results = vector_db_from_pdf.search_by_text(distance_measure=cosine_similarity, k=3, query_text="What ADT can be used to represent a network")
euclidean_results = vector_db_from_pdf.search_by_text(distance_measure=euclidean_similarity, k=3, query_text="What ADT can be used to represent a network")
manhattan_results = vector_db_from_pdf.search_by_text(distance_measure=manhattan_similarity, k=3, query_text="What ADT can be used to represent a network")

print(cosine_results)
print(euclidean_results)
print(manhattan_results)

[('oftrees,forests,andconnectedgraphs.\nProposition 14.11: LetGbeanundirectedgraphwithnverticesandmedges.\n• IfGisconnected,thenm≥n−1.\n• IfGisatree,thenm=n−1.\n• IfGisaforest,thenm≤n−1.\n626 Chapter14. GraphAlgorithms\n14.1.1 The Graph ADT\nA graph is a collection of vertices and edges. Wemodel the abstraction as a com-\nbination of three data types: Vertex, Edge, and Graph. A Vertex is a lightweight\nobject that stores an arbitrary element provided by the user(e.g., an airport code);\nwe assume it supports a method, element(), to retrieve the stored element. An\nEdge also stores an associated object (e.g., a flight number, travel distance, cost),\nretrievedwiththeelement()method. Inaddition,weassumethatanEdgesupports\nthefollowingmethods:\nendpoints(): Return a tuple (u,v) such that vertex u is the origin of\ntheedgeandvertexvisthedestination; foranundirected\ngraph, theorientation isarbitrary.\nopposite(v): Assuming vertex v is one endpoint of the edge (either\noriginordestination),

In [185]:
import pandas as pd
from IPython.display import display


# Assuming your results are lists of (text, score) tuples:
# cosine_results, euclidean_results, manhattan_results

# Convert results to DataFrames
cosine_df = pd.DataFrame(cosine_results, columns=['Text', 'Cosine Similarity'])
euclidean_df = pd.DataFrame(euclidean_results, columns=['Text', 'Euclidean Similarity'])
manhattan_df = pd.DataFrame(manhattan_results, columns=['Text', 'Manhattan Similarity'])

# Merge on the 'Text' column to align results
comparison_df = cosine_df.merge(euclidean_df, on='Text').merge(manhattan_df, on='Text')

# Display the table
print("Query: What ADT can be used to represent a network?")
display(comparison_df)

Text  Cosine Similarity  \
0  oftrees,forests,andconnectedgraphs.\nPropositi...           0.429646   
1   . . . . . . . . . . . . . . . . . . . . . . 6...           0.399592   
2  ation of theaux-\niliaryadjacencymatrixstructu...           0.377727   

   Euclidean Similarity  Manhattan Similarity  
0              0.483574              0.029684  
1              0.477157              0.028792  
2              0.472703              0.028348

##  Two-Stage Retrieval with Cross-Encoder Re-Ranking

In [75]:
from aimakerspace.vectordatabase import VectorDatabase
from aimakerspace.openai_utils.chatmodel import ChatOpenAI

class ReRankingRetrievalAugmentedQAPipeline:
    def __init__(
        self,
        llm: ChatOpenAI,
        vector_db_retriever: VectorDatabase,
        response_style: str = "detailed",
        include_scores: bool = False,
        cross_encoder=None,  # <-- NEW: Cross-encoder for re-ranking
        embedding_model=None # <-- NEW: Bi-encoder for embedding queries
    ) -> None:
        self.llm = llm
        self.vector_db_retriever = vector_db_retriever
        self.response_style = response_style
        self.include_scores = include_scores
        self.cross_encoder = cross_encoder

    def run_pipeline(self, user_query: str, k: int = 4, **system_kwargs) -> dict:
        # ----- Stage 1: Retrieve Top-K with Bi-Encoder -----
        # Get top-k docs (text, score) using vector search
        context_list = self.vector_db_retriever.search_by_text(user_query, k=k)
        top_k_docs = [context for context, _ in context_list]
        # print(f"Initial Context List:"); print_context_list_as_markdown(context_list)
        # ----- Stage 2: Cross-Encoder Re-Ranking -----
        if self.cross_encoder is not None:
            cross_input = [(user_query, doc) for doc in top_k_docs]
            cross_scores = self.cross_encoder.predict(cross_input)
            reranked = sorted(zip(top_k_docs, cross_scores), key=lambda x: x[1], reverse=True)
            # Optionally, update context_list with reranked order and scores
            context_list = [(doc, float(score)) for doc, score in reranked]
            # print(f"Reranked Context List"); print_context_list_as_markdown(context_list)

        # ----- Prompt Construction (as before) -----
        context_prompt = ""
        similarity_scores = []
        for i, (context, score) in enumerate(context_list, 1):
            context_prompt += f"[Source {i}]: {context}\n\n"
            similarity_scores.append(f"Source {i}: {score:.3f}")

        system_params = {
            "response_style": self.response_style,
            "response_length": system_kwargs.get("response_length", "detailed")
        }
        formatted_system_prompt = rag_system_prompt.create_message(**system_params)

        user_params = {
            "user_query": user_query,
            "context": context_prompt.strip(),
            "context_count": len(context_list),
            "similarity_scores": f"Relevance scores: {', '.join(similarity_scores)}" if self.include_scores else ""
        }
        formatted_user_prompt = rag_user_prompt.create_message(**user_params)

        return {
            "response": self.llm.run([formatted_system_prompt, formatted_user_prompt]), 
            "context": context_list,
            "context_count": len(context_list),
            "similarity_scores": similarity_scores if self.include_scores else None,
            "prompts_used": {
                "system": formatted_system_prompt,
                "user": formatted_user_prompt
            }
        }

In [76]:
from sentence_transformers import CrossEncoder

cross_encoder = CrossEncoder("cross-encoder/ms-marco-MiniLM-L-6-v2")

In [77]:
from aimakerspace.openai_utils.chatmodel import ChatOpenAI

chat_openai = ChatOpenAI()

pipeline = ReRankingRetrievalAugmentedQAPipeline(
    llm=chat_openai,
    vector_db_retriever=vector_db_from_pdf,
    response_style="detailed",
    include_scores=True,
    cross_encoder=cross_encoder,
)
result = pipeline.run_pipeline("What is an ADT?", k=5)
print_pipeline_results(result)

Response:


An Abstract Data Type (ADT) is a theoretical concept that defines a data structure purely by what operations can be performed on it, and it is characterized by its public interface and the behaviors it supports. While specific implementations may vary, the key idea is that an ADT does not concern itself with how these operations are implemented; rather, it focuses on the functionality.

For example, in Python, an ADT can be defined using mechanisms such as duck typing, where the programming language assumes that an object supports a known set of behaviors without requiring formal type declarations. This approach allows for flexibility and generic programming, with the understanding that the interpreter will raise errors at runtime if assumptions about the behaviors are incorrect, as detailed in Source 5: "a collective set of behaviors supported by an ADT as its public interface."


Context Count: 5
Similarity Scores: ['Source 1: 2.017', 'Source 2: 0.157', 'Source 3: -0.699', 'Source 4: -1.120', 'Source 5: -8.095']
context 1:


ADT does not provide any way to get a list of all events ordered by the time at
whichtheyoccur,ortosearchforwhicheventoccurredclosesttoaparticulartime.
Infact,thefastperformanceofhash-basedimplementationsofthemapADTrelies
on the intentionally scattering of keys that may seem very “near” to each other in
theoriginaldomain, sothattheyaremoreuniformly distributed inahashtable.
In this section, we introduce an extension known as thesorted map ADT that
includes allbehaviors ofthestandard map,plusthefollowing:
M.find min(): Returnthe(key,value) pairwithminimumkey
(orNone,ifmapisempty).
M.find max(): Returnthe(key,value) pairwithmaximumkey
(orNone,ifmapisempty).
M.find lt(k): Return the (key,value) pair with the greatest key that
isstrictlylessthank(orNone,ifnosuchitemexists).
M.find le(k): Return the (key,value) pair with the greatest key that
is less than or equal to k (or None, if no such item
exists).
M.find gt(k): Return the (key,value) pair with the least key that is

score: 2.016554355621338
context 2:


...

score: -0.6987370252609253
context 4:


Thereareanumberofsimplepropertiesoftrees,forests,andconnectedgraphs.
Proposition 14.11: LetGbeanundirectedgraphwithnverticesandmedges.
• IfGisconnected,thenm≥n−1.
• IfGisatree,thenm=n−1.
• IfGisaforest,thenm≤n−1.
626 Chapter14. GraphAlgorithms
14.1.1 The Graph ADT
A graph is a collection of vertices and edges. Wemodel the abstraction as a com-
bination of three data types: Vertex, Edge, and Graph. A Vertex is a lightweight
object that stores an arbitrary element provided by the user(e.g., an airport code);
we assume it supports a method, element(), to retrieve the stored element. An
Edge also stores an associated object (e.g., a flight number, travel distance, cost),
retrievedwiththeelement()method. Inaddition,weassumethatanEdgesupports
thefollowingmethods:
endpoints(): Return a tuple (u,v) such that vertex u is the origin of
theedgeandvertexvisthedestination; foranundirected
graph, theorientation isarbitrary.
opposite(v): Assuming vertex v is one endpoint of the edge (either

score: -1.1202194690704346
context 5:


collective setofbehaviors supported byanADTasitspublicinterface.
60 Chapter2. Object-OrientedProgramming
Asaprogramming language, Pythonprovides agreatdealoflatitude inregard
to the specification of an interface. Python has a tradition of treating abstractions
implicitly using a mechanism known as duck typing. As an interpreted and dy-
namically typed language, there is no “compile time” checking of data types in
Python, and no formal requirement for declarations of abstract base classes. In-
stead programmers assume that an object supports a set of known behaviors, with
the interpreter raising a run-time error if those assumptions fail. The description
of this as “duck typing” comes from an adage attributed to poet James Whitcomb
Riley, stating that “when Isee abird that walks like aduck and swimslike aduck
andquackslikeaduck, Icallthatbirdaduck.”
Moreformally, Python supports abstract data types using amechanism known

score: -8.094825744628906


In [78]:
result = pipeline.run_pipeline("Give me the code for a doubly linked list in python", k=5)
print_pipeline_results(result)

Response:


The context provides a partial implementation of a doubly linked list in Python, specifically the structure of the `Node` class and the `DoublyLinkedBase` class. Here is the relevant code:

```python
class Node:
    """Lightweight, nonpublic class for storing a doubly linked node."""
    slots = _element, _prev, _next  # streamline memory

    def __init__(self, element, prev, next):
        # initialize node’s fields
        self.element = element  # user’s element
        self.prev = prev  # previous node reference
        self.next = next  # next node reference

class DoublyLinkedBase:
    """A base class providing a doubly linked list representation."""

    class Node:
        """Lightweight, nonpublic class for storing a doubly linked node."""
        # (The definition of this Node class is similar to the one above.)

    def __init__(self):
        """Create an empty list."""
        self.header = self.Node(None, None, None)
        self.trailer = self.Node(None, None, None)
        self.header.next = self.trailer  # trailer is after header
```

This code snippet includes the definition of the `Node` class for a doubly linked list and the beginning of the `DoublyLinkedBase` class that constructs the list.


Context Count: 5
Similarity Scores: ['Source 1: 4.526', 'Source 2: 4.310', 'Source 3: 2.867', 'Source 4: 2.027', 'Source 5: -0.304']
context 1:


listdoublylinked(aswedoinSection7.3).
7.1. SinglyLinkedLists 261
7.1.1 Implementing a Stack with a Singly Linked List
In this section, wedemonstrate use ofasingly linked list byproviding acomplete
Python implementation of the stack ADT (see Section 6.1). Indesigning such an
implementation,weneedtodecidewhethertomodelthetopofthestackatthehead
oratthetailofthelist. Thereisclearlyabestchoicehere;wecanefficientlyinsert
and delete elements in constant time only at the head. Since all stack operations
affectthetop,weorientthetopofthestackattheheadofourlist.
Torepresentindividualnodesofthelist,wedevelopalightweight Nodeclass.
This class will never be directly exposed to the user of our stack class, so we will
formally define it as a nonpublic, nested class of our eventual LinkedStack class
(see Section 2.5.1 for discussion of nested classes). The definition of the Node
classisshowninCodeFragment7.4.
class Node:
”””Lightweight, nonpublic class for storing a singly linked node.”””

score: 4.525667667388916
context 2:


...

score: 2.8671631813049316
context 4:


48 if self.is empty():
49 newest. next = newest # initialize circularly
50 else:
51 newest. next = self. tail. next # new node points to head
52 self. tail. next = newest # old tail points to new node
53 self. tail = newest # new node becomes the tail
54 self. size += 1
55
56 def rotate(self):
57 ”””Rotate front element to the back of the queue.”””
58 if self. size > 0:
59 self. tail = self. tail. next # old head becomes new tail
Code Fragment7.10: Implementation of a CircularQueue class, using a circularly
linkedlistasstorage (continued fromCodeFragment7.9).
270 Chapter7. LinkedLists
7.3 Doubly Linked Lists
Inasingly linked list, eachnode maintains areference tothenode thatisimmedi-
ately after it. We have demonstrated the usefulness of such arepresentation when
managing a sequence of elements. However, there are limitations that stem from
the asymmetry of a singly linked list. In the opening of Section 7.1, we empha-

score: 2.0266740322113037
context 5:


31
32 def delete node(self, node):
33 ”””Delete nonsentinel node from the list and return its element.”””
34 predecessor = node. prev
35 successor = node. next
36 predecessor. next = successor
37 successor. prev = predecessor
38 self. size −= 1
39 element = node. element # record deleted element
40 node. prev = node. next = node. element = None # deprecate node
41 return element # return deleted element
CodeFragment7.12: Abaseclassformanagingadoublylinked list.
7.3. DoublyLinkedLists 275
Theothertwomethodsofourclassarethenonpublicutilities, insert between
and delete node. These provide generic support for insertions and deletions, re-
spectively, butrequire oneormorenodereferences asparameters. Theimplemen-
tationofthe insert betweenmethodismodeleduponthealgorithmthatwasprevi-
ouslyportrayedinFigure7.11. Itcreatesanewnode,withthatnode’sfieldsinitial-
ized tolink to the specified neighboring nodes. Thenthe fields ofthe neighboring

score: -0.30415573716163635


In [79]:
result = pipeline.run_pipeline("What data structure would be used for a text editor's undo mechanism? ", k=5)
print_pipeline_results(result)

Response:


The data structure used for a text editor's undo mechanism is a stack. This is indicated in Source 1, which explains that text editors usually provide an "undo" operation that can be accomplished by keeping text changes in a stack. The stack allows users to revert to former states of a document, effectively managing the sequence of editing operations.


Context Count: 5
Similarity Scores: ['Source 1: 0.894', 'Source 2: -8.898', 'Source 3: -9.534', 'Source 4: -9.814', 'Source 5: -10.328']
context 1:


inastack.Eachtimeauservisitsanewsite,thatsite’saddressis“pushed”ontothe
stackofaddresses. Thebrowserthenallowstheuserto“pop”backtopreviously
visitedsitesusingthe“back”button.
Example 6.2: Texteditorsusuallyprovidean“undo”mechanismthatcancelsre-
centeditingoperationsandrevertstoformerstatesofadocument.Thisundooper-
ationcanbeaccomplishedbykeepingtextchangesinastack.
Figure6.1: A schematic drawing of a PEZ® dispenser; a physical implementation
ofthestackADT.(PEZ® isaregistered trademarkofPEZCandy,Inc.)
230 Chapter6. Stacks,Queues,andDeques
6.1.1 The Stack Abstract Data Type
Stacks are the simplest of all data structures, yet they are also among the most
important. Theyareusedinahostofdifferent applications, andasatoolformany
more sophisticated data structures and algorithms. Formally, astack isan abstract
datatype(ADT)suchthataninstanceSsupports thefollowingtwomethods:
S.push(e): AddelementetothetopofstackS.
S.pop(): RemoveandreturnthetopelementfromthestackS;

score: 0.8940330147743225
context 2:


...

score: -9.534271240234375
context 4:


C-7.41 ExerciseC-5.29introduces thenotion ofanaturaljoinoftwodatabases.
Describeandanalyzeanefficientalgorithmforcomputingthenaturaljoin
ofalinkedlistAofnpairsandalinkedlistBofmpairs.
C-7.42 Write a Scoreboard class that maintains the top 10 scores for a game ap-
plication using a singly linked list, rather than the array that was used in
Section5.5.1.
C-7.43 Describe amethod forperforming acardshuffleofalistof2nelements,
byconverting itintotwolists. Acardshuffleisapermutationwherealist
Liscutintotwolists,L andL ,whereL isthefirsthalfofLandL isthe
1 2 1 2
second half of L, and then these two lists are merged into one by taking
thefirstelementinL ,thenthefirstelementinL ,followedbythesecond
1 2
elementinL ,thesecondelementinL ,andsoon.
1 2
Projects
P-7.44 Write a simple text editor that stores and displays a string of characters
usingthepositional listADT,togetherwithacursorobjectthathighlights
a position in this string. A simple interface is to print the string and then

score: -9.814085960388184
context 5:


thelinesreadfromthefileinreverseorder,thentheoriginallastlinewouldbefol-
lowed(withoutnewline)bytheoriginalsecond-to-lastline. Inourimplementation,
weensurethattherewillbeaseparating newlineintheresult.
The idea of using a stack to reverse a data set can be applied toother types of
sequences. Forexample, Exercise R-6.5 explores the use of astack to provide yet
anothersolution forreversingthecontents ofaPythonlist(arecursivesolution for
this goal was discussed in Section 4.4.1). A more challenging task is to reverse
the order in which elements are stored within a stack. If we were to move them
from one stack to another, they would be reversed, but if we were to then replace
themintotheoriginalstack,theywouldbereversedagain,therebyrevertingtotheir
original order. ExerciseC-6.18explores asolution forthistask.
236 Chapter6. Stacks,Queues,andDeques
6.1.4 Matching Parentheses and HTML Tags
In this subsection, we explore two related applications of stacks, both of which

score: -10.328374862670898


In [73]:
result = pipeline.run_pipeline("Tell me about the adapter pattern for a stack data structure", k=5)
print_pipeline_results(result)

Response:


The adapter pattern is a design pattern used to modify an existing class so that its methods match those of a related, but different, class or interface. In the context of the stack abstract data type (ADT), this pattern can be applied by defining a new class that contains an instance of an existing class (such as Python's list) as a hidden field. Each method of this new class is then implemented using methods of this hidden instance variable.

For instance, in adapting Python's list class to function as a stack, we can establish method correspondences as shown in Table 6.1 from the context. The following mappings illustrate this adaptation:

- The stack operation `S.push(e)` corresponds to `L.append(e)` from the list.
- The stack operation `S.pop()` corresponds to `L.pop()`.
- The stack operation `S.top()` corresponds to accessing the last element with `L[-1]`.
- The stack method `S.is_empty()` checks if the list is empty with `len(L) == 0`.
- The stack length `len(S)` corresponds to `len(L)`.

By creating a new class that encapsulates a Python list and implements the stack interface, we provide a convenient way to utilize list functionalities while maintaining the stack's abstraction. This approach emphasizes the conceptual distinction between a stack and a list and helps achieve a clear interface based on the intended functionalities of the stack ADT, as noted in the sources.


Context Count: 5
Similarity Scores: ['Source 1: 4.810', 'Source 2: 2.200', 'Source 3: -3.093', 'Source 4: -3.239', 'Source 5: -4.126']
context 1:


rightmostcell.
Although a programmer could directly use the list class in place of a formal
stack class, lists also include behaviors (e.g., adding or removing elements from
arbitrarypositions) thatwouldbreaktheabstraction thatthestackADTrepresents.
Also,theterminologyusedbythelistclassdoesnotpreciselyalignwithtraditional
nomenclature for a stack ADT, in particular the distinction between append and
push. Instead,wedemonstratehowtousealistforinternalstoragewhileproviding
apublicinterface consistent withastack.
The Adapter Pattern
The adapter design pattern applies to any context where we effectively want to
modifyanexisting class sothatitsmethods matchthose ofarelated, butdifferent,
class or interface. One general way to apply the adapter pattern is to define a new
class in such a way that it contains an instance of the existing class as a hidden
field, and then to implement each method of the new class using methods of this

score: 4.810179710388184
context 2:


...

score: -3.0930731296539307
context 4:


inastack.Eachtimeauservisitsanewsite,thatsite’saddressis“pushed”ontothe
stackofaddresses. Thebrowserthenallowstheuserto“pop”backtopreviously
visitedsitesusingthe“back”button.
Example 6.2: Texteditorsusuallyprovidean“undo”mechanismthatcancelsre-
centeditingoperationsandrevertstoformerstatesofadocument.Thisundooper-
ationcanbeaccomplishedbykeepingtextchangesinastack.
Figure6.1: A schematic drawing of a PEZ® dispenser; a physical implementation
ofthestackADT.(PEZ® isaregistered trademarkofPEZCandy,Inc.)
230 Chapter6. Stacks,Queues,andDeques
6.1.1 The Stack Abstract Data Type
Stacks are the simplest of all data structures, yet they are also among the most
important. Theyareusedinahostofdifferent applications, andasatoolformany
more sophisticated data structures and algorithms. Formally, astack isan abstract
datatype(ADT)suchthataninstanceSsupports thefollowingtwomethods:
S.push(e): AddelementetothetopofstackS.
S.pop(): RemoveandreturnthetopelementfromthestackS;

score: -3.2389111518859863
context 5:


begins with an empty list and expands as needed. In the analysis of lists from
Section 5.4.1, weemphasized that itismoreefficient in practice toconstruct alist
with initial length n than it is to start with an empty list and append n items (even
thoughbothapproaches runinO(n)time).
As an alternate model for a stack, wemight wish for the constructor to accept
aparameterspecifying themaximumcapacityofastackandtoinitializethe data
member to a list of that length. Implementing such a model requires significant
changes relative to Code Fragment 6.2. The size of the stack would no longer be
synonymouswiththelengthofthelist,andpushesandpopsofthestackwouldnot
require changing the length of the list. Instead, wesuggestmaintaining aseparate
integer as an instance variable that denotes the current number of elements in the
stack. Detailsofsuchanimplementation areleftasExerciseC-6.17.
6.1. Stacks 235
6.1.3 Reversing Data Using a Stack

score: -4.126374244689941


In [80]:
result = pipeline.run_pipeline("Why is recursion an important concept to understand when learning data structures and algorithms? ", k=5)
print_pipeline_results(result)

Response:


Recursion is an important concept in the study of data structures and algorithms because it provides an elegant and powerful alternative for performing repetitive tasks, making it essential for expressing various forms of computation. The context indicates that modern programming languages support functional recursion and characterizes recursion as a key technique used prominently in the study of data structures and algorithms. Specific examples highlighted in the text, such as the factorial function, binary search, and the recursive structure of filesystem directories, demonstrate its applicability in solving complex problems efficiently (Sources 1 and 2). Furthermore, the chapter emphasizes that recursion techniques will be revisited in several later chapters, illustrating its foundational role in understanding and effectively managing complex data structures (Source 1).


Context Count: 5
Similarity Scores: ['Source 1: 4.415', 'Source 2: 0.524', 'Source 3: -0.413', 'Source 4: -1.657', 'Source 5: -3.277']
context 1:


dollinsideit.
In computing, recursion provides an elegant and powerful alternative for per-
forming repetitive tasks. In fact, a few programming languages (e.g., Scheme,
Smalltalk) do not explicitly support looping constructs and instead rely directly
on recursion to express repetition. Most modern programming languages support
functional recursion using the identical mechanism that is used to support tradi-
tional forms of function calls. When one invocation of the function make a recur-
sivecall,thatinvocation issuspended untiltherecursivecallcompletes.
Recursion is an important technique in the study of data structures and algo-
rithms. We will use it prominently in several later chapters of this book (most
notably, Chapters 8 and 12). In this chapter, we begin with the following four il-
lustrative examplesoftheuseofrecursion, providing aPythonimplementation for
each.
• The factorial function (commonly denoted as n!) is a classic mathematical

score: 4.414797782897949
context 2:


...

score: -0.41347819566726685
context 4:


time outside the loop, and that the overall number of operations due to the loop
isO(n). Summingallofthesebounds, theoverallnumberofoperations isO(n).
The argument we have made is more advanced than with the earlier examples
of recursion. The idea that we can sometimes get a tighter bound on a series of
operations by considering the cumulative effect, rather than assuming that each
achieves a worst case is a technique called amortization; we will see a further
example of such analysis in Section 5.3. Furthermore, a file system is an implicit
exampleofadatastructure knownasatree, andourdiskusagealgorithm isreally
a manifestation of a more general algorithm known as atree traversal. Trees will
be the focus of Chapter 8, and our argument about the O(n) running time of the
diskusagealgorithm willbegeneralized fortreetraversals inSection8.4.
4.3. RecursionRunAmok 165
4.3 Recursion Run Amok
Althoughrecursionisaverypowerfultool,itcaneasilybemisusedinvariousways.

score: -1.6572202444076538
context 5:


4.1.3 Binary Search . . . . . . . . . . . . . . . . . . . . . . . . 155
4.1.4 File Systems . . . . . . . . . . . . . . . . . . . . . . . . . 157
4.2 Analyzing Recursive Algorithms . . . . . . . . . . . . . . . 161
4.3 Recursion Run Amok . . . . . . . . . . . . . . . . . . . . . 165
4.3.1 Maximum Recursive Depth in Python . . . . . . . . . . . 168
4.4 Further Examples of Recursion . . . . . . . . . . . . . . . . 169
4.4.1 Linear Recursion . . . . . . . . . . . . . . . . . . . . . . . 169
4.4.2 Binary Recursion . . . . . . . . . . . . . . . . . . . . . . 174
4.4.3 Multiple Recursion . . . . . . . . . . . . . . . . . . . . . 175
4.5 Designing Recursive Algorithms . . . . . . . . . . . . . . . 177
4.6 Eliminating Tail Recursion . . . . . . . . . . . . . . . . . . 178
4.7 Exercises . . . . . . . . . . . . . . . . . . . . . . . . . . . . 180
149
Oneway todescribe repetition within a computer program is the use ofloops,

score: -3.277118682861328


# Exploring Metadata Storage and Filtering for improved RAG

Pre-filtering (e.g., by chapter or topic) significantly improves retrieval speed and context relevance.
Example Metadata:
- Chapter / Section / Subsection
Easily filter to relevant topics, e.g. filter to “Chapter 5” for sorting/search  ￼ ￼.
- Page Number or Range
Useful when pinpointing specific content in precise recall tasks.
- Code Examples Included (boolean)
Great for developer queries like “show code for quicksort.”
- Topic Tag (e.g. “Trees”, “Sorting”, “Recursion”)
Aligns with broad content categorizations.
- Complexity / Difficulty Level
e.g. Basic, Intermediate, Advanced — helpful for tailoring answers to user learning levels.
- Prerequisites or Related Concepts
e.g. requires_knowledge_of: recursion — filters for users building on prior content.

Post-filtering ensures finer-grained control over what content actually gets used in your generation prompts.
Example Metadata
- Author / Contributor
If multiple authors or guest content appear, enable bias/filter control.
- Publication/Revision Date
Favor newer content or align temporally.
- Example Count
Prioritize chunks rich in examples or explanations.
- Estimated Length (in tokens)
Filter out overly short or redundant chunks.
- Chunk Position within Section
e.g., 1, 2, 3 to prefer openers over definitions/examples.

We must start by modifying our chunking, such that we generate metadata as we parse the PDF

In [4]:
import fitz  # PyMuPDF

class PDFFileLoader:
    def __init__(self, path):
        self.path = path

    def load_file(self):
        docs = []
        doc = fitz.open(self.path)
        # Get Table of Contents entries: [(level, title, start_page), ...]
        toc = doc.get_toc()  
        print(toc)
        # Build page-to-TOC mapping
        page_map = {}  # maps page_num → (chapter, section)
        stack = []
        for level, title, start in toc:
            stack = [ (lvl, t, sp) for (lvl, t, sp) in stack if lvl < level ]
            stack.append((level, title, start))
            # Assign chapters/sections until next TOC entry
            end = doc.page_count
            for lvl2, _, start2 in toc:
                if lvl2 <= level and start2 > start:
                    end = min(end, start2 - 1)
            for p in range(start - 1, end):
                chapter = stack[0][1] if stack else None
                section = stack[1][1] if len(stack) > 1 else None
                page_map[p] = {"chapter": chapter, "section": section}

        # Extract text page-by-page
        for i, page in enumerate(doc):
            raw = page.get_text("text", sort=True)
            chunk = {
                "text": raw,
                "metadata": {
                    "page": i + 1,
                    **page_map.get(i, {"chapter": None, "section": None})
                }
            }
            docs.append(chunk)
        return docs

loader = PDFFileLoader("data/Fundementals of Python_ DSA [2nd Edition].pdf")
chunks = loader.load_file()

[[1, 'Cover', 1], [1, 'Title Page', 3], [1, 'Copyright Page', 4], [1, 'Preface', 7], [1, 'Contents', 13], [1, '1 Python Primer', 23], [2, '1.1 Python Overview', 24], [3, '1.1.1 The Python Interpreter', 24], [3, '1.1.2 Preview of a Python Program', 25], [2, '1.2 Objects in Python', 26], [3, '1.2.1 Identifiers, Objects, and the Assignment Statement', 26], [3, '1.2.2 Creating and Using Objects', 28], [3, '1.2.3 Python’s Built-In Classes', 29], [2, '1.3 Expressions, Operators, and Precedence', 34], [3, '1.3.1 Compound Expressions and Operator Precedence', 39], [2, '1.4 Control Flow', 40], [3, '1.4.1 Conditionals', 40], [3, '1.4.2 Loops', 42], [2, '1.5 Functions', 45], [3, '1.5.1 Information Passing', 46], [3, '1.5.2 Python’s Built-In Functions', 50], [2, '1.6 Simple Input and Output', 52], [3, '1.6.1 Console Input and Output', 52], [3, '1.6.2 Files', 53], [2, '1.7 Exception Handling', 55], [3, '1.7.1 Raising an Exception', 56], [3, '1.7.2 Catching an Exception', 58], [2, '1.8 Iterators and

In [91]:
len(chunks)

770

In [103]:
display(Markdown(chunks[101]["text"]))

80                                   Chapter 2. Object-Oriented Programming

      2.3.5  Example: Range Class

        As the ﬁnal example for this section, we develop our own implementation of a
            class that mimics Python’s built-in range class. Before introducing our class, we
           discuss the history of the built-in version. Prior to Python 3 being released, range
         was implemented as a function, and it returned a list instance with elements in
           the speciﬁed range.  For example, range(2, 10, 2) returned the list [2, 4, 6, 8].
          However, a typical use of the function was to support a for-loop syntax, such as
           for k in range(10000000). Unfortunately, this caused the instantiation and initial-
            ization of a list with the range of numbers. That was an unnecessarily expensive
            step, in terms of both time and memory usage.
            The mechanism used to support ranges in Python 3 is entirely different (to be
               fair, the “new” behavior existed in Python 2 under the name xrange).  It uses a
            strategy known as lazy evaluation. Rather than creating a new list instance, range
              is a class that can effectively represent the desired range of elements without ever
            storing them explicitly in memory. To better explore the built-in range class, we
         recommend that you create an instance as r = range(8, 140, 5). The result is a
            relatively lightweight object, an instance of the range class, that has only a few
           behaviors. The syntax len(r) will report the number of elements that are in the
           given range (27, in our example). A range also supports the   getitem   method,
          so that syntax r[15] reports the sixteenth element in the range (as r[0] is the ﬁrst
           element). Because the class supports both   len   and   getitem    , it inherits
           automatic support for iteration (see Section 2.3.4), which is why it is possible to
           execute a for loop over a range.
            At this point, we are ready to demonstrate our own version of such a class. Code
          Fragment 2.6 provides a class we name Range (so as to clearly differentiate it from
             built-in range). The biggest challenge in the implementation is properly computing
           the number of elements that belong in the range, given the parameters sent by the
             caller when constructing a range. By computing that value in the constructor, and
            storing it as self. length, it becomes trivial to return it from the   len   method. To
           properly implement a call to   getitem   (k), we simply take the starting value of
           the range plus k times the step size (i.e., for k=0, we return the start value). There
           are a few subtleties worth examining in the code:

            • To properly support optional parameters, we rely on the technique described
              on page 27, when discussing a functional version of range.

            • We compute the number of elements in the range as
               max(0, (stop −start + step −1) // step)
                       It is worth testing this formula for both positive and negative step sizes.

            • The   getitem   method properly supports negative indices by converting
               an index −k to len(self)−k before computing the result.

# Using Page by Page Chunking

TODO:
- Chunking
    - Create an index, mapping each chunk to a chapter and section:
    {"chapter name": [list of embeddings], "section_name": [list of embeddings]}
    - Create a new cal
- Pre-Filtering

In [5]:
chunks[0]

{'text': '', 'metadata': {'page': 1, 'chapter': 'Cover', 'section': None}}

In [113]:
vector_db_metadata = VectorDatabase()
vector_db_metadata = asyncio.run(vector_db_metadata.abuild_from_list(chunks))










# 

BadRequestError: Error code: 400 - {'error': {'message': "'$.input' is invalid. Please check the API reference: https://platform.openai.com/docs/api-reference.", 'type': 'invalid_request_error', 'param': None, 'code': None}}

In [5]:
from aimakerspace.vectordatabase import VectorDatabaseWithMetadata

vector_db_with_metadata = VectorDatabaseWithMetadata()
vector_db_with_metadata.build_chunk_index(chunks)
print("Chunk Index:")
for k, v in vector_db_with_metadata.chunk_index.items():
    print(f"{k}: {v}")

Chunk Index:
('chapter', 'Cover'): ['', '']
('chapter', 'Title Page'): ['Data Structures and\nAlgorithms in Python\n\n       Michael T. Goodrich\n        Department of Computer Science\n          University of California, Irvine\n\n        Roberto Tamassia\n        Department of Computer Science\n            Brown University\n\n      Michael H. Goldwasser\nDepartment of Mathematics and Computer Science\n              Saint Louis University']
('chapter', 'Copyright Page'): ['         VP & PUBLISHER                     Don Fowley\n          EXECUTIVE EDITOR                       Beth Lang Golub\n          EDITORIAL PROGRAM ASSISTANT          Katherine Willis\n         MARKETING MANAGER                     Christopher Ruel\n          DESIGNER                                   Kenji Ngieng\n          SENIOR PRODUCTION MANAGER            Janis Soo\n          ASSOCIATE PRODUCTION MANAGER      Joyce Poh\n\nThis book was set in LaTEX by the authors. Printed and bound by Courier Westford.\nThe 

In [7]:
for k, v in vector_db_with_metadata.chunk_index.items():
    print(f"{k}: {len(v)}")

('chapter', 'Cover'): 2
('chapter', 'Title Page'): 1
('chapter', 'Copyright Page'): 3
('chapter', 'Preface'): 6
('chapter', 'Contents'): 10
('chapter', '1 Python Primer'): 55
('section', '1 Python Primer - 1.1 Python Overview'): 2
('section', '1 Python Primer - 1.2 Objects in Python'): 8
('section', '1 Python Primer - 1.3 Expressions, Operators, and Precedence'): 6
('section', '1 Python Primer - 1.4 Control Flow'): 5
('section', '1 Python Primer - 1.5 Functions'): 7
('section', '1 Python Primer - 1.6 Simple Input and Output'): 3
('section', '1 Python Primer - 1.7 Exception Handling'): 6
('section', '1 Python Primer - 1.8 Iterators and Generators'): 3
('section', '1 Python Primer - 1.9 Additional Python Conveniences'): 4
('section', '1 Python Primer - 1.10 Scopes and Namespaces'): 2
('section', '1 Python Primer - 1.11 Modules and the Import Statement'): 3
('section', '1 Python Primer - 1.12 Exercises'): 5
('chapter', '2 Object-Oriented Programming'): 53
('section', '2 Object-Oriented Pr

In [10]:
import asyncio
from aimakerspace.vectordatabase import VectorDatabaseWithMetadata
from aimakerspace.openai_utils.embedding import EmbeddingModel

vector_db_with_metadata = VectorDatabaseWithMetadata()
vector_db_with_metadata.build_chunk_index(chunks)

# Use async abuild_from_list to insert all chunks and their embeddings
vector_db_with_metadata = asyncio.run(vector_db_with_metadata.abuild_from_list(chunks[:10]))

query = "How do list comprehensions work in Python?"
results = vector_db_with_metadata.search_by_text(query, k=3)

print(f"Query: {query}")
print("Top 3 results (with similarity scores):")
for text, score in results:
    print(f"Score: {score:.4f}\nText: {text}\n---")

BadRequestError: Error code: 400 - {'error': {'message': "'$.input' is invalid. Please check the API reference: https://platform.openai.com/docs/api-reference.", 'type': 'invalid_request_error', 'param': None, 'code': None}}

In [8]:
len(chunks)

770